# .dat to .csv
The purpose of this tool is to convert _.dat_ files into _.csv_ files where each row is a sample to be analyzed.

The .dat files are obtained by running the *cap2dat* program on _.pcap_ files.

Firstly the data is loaded to a numpy array.

In [1]:
import os
import numpy as np
from collections import defaultdict, deque
from scalogram import *
import pandas as pd
from sklearn.externals import joblib 
import re

base_url = '../../../shared/'
sampling_interval = '1s' # 1s or 01s
sample_size = 30 # number of intervals for each sample
all_data = np.zeros(5)

def split_number(s):
    return list(filter(None, re.split(r'(\d+)', s)))

for path, subdirs, files in os.walk(base_url):
    for name in files:
        if os.path.basename(path) != sampling_interval:
            continue
        
        print(os.path.join(path, name))
        
        #[up_n_packets, up_n_bytes, up_flag, down_n_packets, down_n_bytes, down_flag]
        data = np.loadtxt(os.path.join(path, name))
        data = np.delete(data, [2,5], 1)
        label = np.full((np.size(data, 0), 1), split_number(name.split('.')[0])[0])
        data = np.hstack((data, label))
        all_data = np.vstack((all_data, data))

../../../shared/openvpn/netflix/dat/1s/netflix-openvpn.pcapng_1.00s.dat
../../../shared/openvpn/youtube/dat/1s/youtube-openvpn.pcapng_1.00s.dat
../../../shared/openvpn/acestream/dat/1s/acestream-openvpn.pcapng_1.00s.dat
../../../shared/openvpn/twitch/dat/1s/twitch-openvpn.pcapng_1.00s.dat
../../../shared/normal/netflix/dat/1s/netflix11.pcapng_1.00s.dat
../../../shared/normal/netflix/dat/1s/netflix2.pcapng_1.00s.dat
../../../shared/normal/netflix/dat/1s/netflix4.pcapng_1.00s.dat
../../../shared/normal/netflix/dat/1s/netflix10.pcapng_1.00s.dat
../../../shared/normal/netflix/dat/1s/netflix12.pcapng_1.00s.dat
../../../shared/normal/netflix/dat/1s/netflix3.pcapng_1.00s.dat
../../../shared/normal/youtube/dat/1s/youtube1.pcapng_1.00s.dat
../../../shared/normal/youtube/dat/1s/youtube4.pcapng_1.00s.dat
../../../shared/normal/youtube/dat/1s/youtube3.pcapng_1.00s.dat
../../../shared/normal/youtube/dat/1s/youtube2.pcapng_1.00s.dat
../../../shared/normal/youtube/dat/1s/youtube51.pcapng_1.00s.dat
..

# Normalize

Apply a standard scaler to all of the data and save it (we will need it for live classification).

In [2]:
from sklearn.preprocessing import StandardScaler

to_scale = all_data[:, :-1]
scaler = StandardScaler()
scaled = scaler.fit_transform(np.asarray(to_scale))
scaled = np.hstack((scaled.astype(float), np.matrix(all_data[:, -1]).T))
joblib.dump(scaler, '../models/std_scaler_' + sampling_interval + '.sav')


/home/agro/work/thesis/env/lib/python3.6/site-packages/sklearn/utils/validation.py:475: DataConversionWarning: Data with input dtype <U32 was converted to float64 by StandardScaler.
  warnings.warn(msg, DataConversionWarning)


['../models/std_scaler_1s.sav']

In [40]:
zeros = scaled[0].tolist()[0][:-1]
zeros = [float(i) for i in zeros]
zeros

[-0.4701345845496797,
 -0.16422699175792135,
 -0.3384386570861066,
 -0.3671146221100995]

# Divide data into chunks

In [4]:
def get_info(data):
    info = []
    up = defaultdict(list)
    down = defaultdict(list)
    result = {}
    count = 0
    current_label = data[1, 4]
    for interval_unit in data[1:]:
        if current_label != interval_unit.item(4):
            current_label = interval_unit.item(4)
        up['packet_count'].append(float(interval_unit.item(0)))
        up['byte_count'].append(float(interval_unit.item(1)))
        down['packet_count'].append(float(interval_unit.item(2)))
        down['byte_count'].append(float(interval_unit.item(3)))
        count+=1
        if count >= sample_size:
            result['up'] = up
            result['down'] = down
            info.append((result, current_label))
            up = defaultdict(list)
            down = defaultdict(list)
            result = {}
            count = 0
    return info
info = get_info(scaled)

# Scalogram scales

In [5]:
#Scalogram
N = sample_size
dj=1/128
s0=2
J=1/dj * np.log2(0.5*N/s0)
scales=s0*2**(np.arange(J)*dj)

Get scalogram data

In [6]:
from scipy.signal import argrelextrema

def calc_scalogram(data, scales):
    S,scales= scalogramCWT(data,scales)
    return S
def show_scalo(data, scales, colors):
    for i in range (0, len(data)):
        plt.plot(scales, data[i], colors[i], lw=3)
    plt.show()
    
# Get top X spikes from scalogram, sorted by value
def get_spikes(scalo, comparator):
    len(scalo)
    spikes = deque([(-1,-1)] * 5, maxlen=5)
    #aux = argrelextrema(scalo, comparator, order=int(len(scalo)/10))
    aux = argrelextrema(scalo, comparator)
    if aux[0].size:
        for x in np.nditer(aux) or []:
            spikes.append((scalo[x], scales[x]))
    ordered = sorted(spikes, key=lambda x: x[1], reverse=True)
    values = np.hstack(zip(*ordered))
    return values

scalos_up = []
scalos_down = []
for sample in info:
    print(sample)
    scalos_up.append(
        (
            (calc_scalogram((sample[0]['up']['byte_count']), scales), 
             calc_scalogram(np.asarray(sample[0]['up']['packet_count']), scales)
            ),
             sample[1]
        )
    )
    scalos_down.append(
        (    
            (calc_scalogram(np.asarray(sample[0]['down']['byte_count']), scales),
             calc_scalogram(np.asarray(sample[0]['down']['packet_count']), scales)
            ),
            sample[1]
        )
    )

({'up': defaultdict(<class 'list'>, {'packet_count': [20.927229396454106, 23.767003011216953, 17.85631141769893, 7.628173311038559, 6.761381946067341, 4.615041423281467, 7.306222232620677, 4.895716722415004, 8.87470184542574, 5.688211684674404, 4.4664486178578295, 4.66457235842268, 1.9073503022285185, 2.4191699653543806, 1.345999703961444, 1.213917210251544, 3.6904639673121675, 3.9711392664457046, 4.317855812434193, 4.2518145655792425, 4.317855812434193, 1.725736873377406, 0.636056300270732, -0.4701345845496797, 0.5535047417020446, -0.4701345845496797, 0.30585006599598225, -0.4701345845496797, 0.45444287141961964, -0.4701345845496797], 'byte_count': [61.03625942422069, 69.60499687094804, 52.590431378544274, 22.534105603647962, 18.964486562626426, 14.402340404329964, 22.212067652990577, 15.281956765312541, 26.735896105170944, 17.563239289433717, 14.046262064746903, 14.62217139674806, 6.679620580605606, 7.758807142140734, 5.063712126019773, 4.683498371999577, 11.812506259878251, 12.62046

({'up': defaultdict(<class 'list'>, {'packet_count': [-0.42060364940846723, 0.0747057020036574, -0.4701345845496797, -0.04086647999250501, 0.10772632543113238, 0.00866445514870745, -0.4701345845496797, 0.17376757228608233, -0.4701345845496797, 0.8506903525493194, -0.4701345845496797, 0.04168507857618243, -0.4701345845496797, 1.3294893922477065, -0.4701345845496797, 0.2728294425685073, -0.4701345845496797, 0.15725726057234485, -0.4701345845496797, 0.10772632543113238, -0.4701345845496797, 0.04168507857618243, -0.4701345845496797, 0.14074694885860736, -0.4701345845496797, 0.8011594174081069, -0.4701345845496797, -0.10690772684745498, -0.4701345845496797, 0.14074694885860736], 'byte_count': [-0.05514227205597675, 1.404154743575387, -0.16422699175792135, 0.8923123745835649, 0.7070365198647739, 1.214047866565289, -0.16422699175792135, 1.689315059090534, -0.16422699175792135, 3.6291204252534954, -0.16422699175792135, 1.309101305070338, -0.16422699175792135, 5.007395283576705, -0.164226991757

({'up': defaultdict(<class 'list'>, {'packet_count': [-0.45362427283594225, 0.8837109759767944, -0.4701345845496797, 0.25631913085476976, -0.4701345845496797, 0.2398088191410323, -0.4701345845496797, 0.30585006599598225, -0.4701345845496797, 0.3718913128509322, -0.4701345845496797, 0.5535047417020446, -0.4701345845496797, 0.32236037770971976, -0.4701345845496797, 0.2728294425685073, -0.45362427283594225, 0.9827728462592192, -0.4701345845496797, 0.6855872354119444, -0.4701345845496797, 0.30585006599598225, -0.4701345845496797, 0.32236037770971976, -0.4701345845496797, 0.32236037770971976, -0.4701345845496797, 0.35538100113719473, -0.4701345845496797, 0.15725726057234485], 'byte_count': [-0.11856185969439102, 3.732963986949087, -0.16422699175792135, 1.9269486553531567, -0.16422699175792135, 1.8794219361006321, -0.16422699175792135, 2.0695288131107303, -0.16422699175792135, 2.2596356901208283, -0.16422699175792135, 2.783361052060408, -0.16422699175792135, 2.1170555323632545, -0.1642269917

({'up': defaultdict(<class 'list'>, {'packet_count': [-0.2224799088436174, 0.25631913085476976, -0.4701345845496797, 0.3388706894234572, -0.4701345845496797, 0.4874634948470946, -0.4701345845496797, 0.28933975428224473, -0.4701345845496797, 0.9745176904023506, -0.46187942869281096, 0.2728294425685073, -0.4701345845496797, 0.28933975428224473, -0.4701345845496797, 0.2398088191410323, -0.4701345845496797, 0.2067881957135573, -0.4701345845496797, 0.3388706894234572, -0.4701345845496797, 0.42142224799214467, -0.4701345845496797, 0.28933975428224473, -0.4701345845496797, 0.7681387939806319, -0.4701345845496797, 0.45444287141961964, -0.4701345845496797, 0.2728294425685073], 'byte_count': [0.011207794357494178, 1.9269486553531567, -0.16422699175792135, 2.164582251615779, -0.16422699175792135, 2.5923227248884997, -0.16422699175792135, 2.0220020938582057, -0.16422699175792135, 3.9944025254344813, -0.14236680191716267, 1.9747099879923027, -0.16422699175792135, 2.0220020938582057, -0.164226991757

({'up': defaultdict(<class 'list'>, {'packet_count': [-0.2224799088436174, 0.5535047417020446, -0.4701345845496797, 0.28933975428224473, -0.4701345845496797, 0.3884016245646697, -0.4701345845496797, 0.14074694885860736, -0.4701345845496797, 0.12423663714486988, -0.4701345845496797, 0.9497522228317443, -0.4701345845496797, 0.00866445514870745, -0.4701345845496797, 0.15725726057234485, -0.4701345845496797, 0.735118170553157, -0.4701345845496797, 0.02517476686244494, -0.4701345845496797, 0.058195390289919914, -0.4701345845496797, 0.0747057020036574, -0.4701345845496797, 0.09121601371739489, -0.4701345845496797, 0.04168507857618243, -0.4701345845496797, 0.04168507857618243], 'byte_count': [0.011207794357494178, 2.747071263519348, -0.16422699175792135, 2.0220020938582057, -0.16422699175792135, 2.3071624093733525, -0.16422699175792135, 1.594261620585485, -0.16422699175792135, 1.5467349013329605, -0.16422699175792135, 3.923070863959185, -0.16422699175792135, 1.214047866565289, -0.164226991757

...

({'up': defaultdict(<class 'list'>, {'packet_count': [-0.43711396112220474, -0.4701345845496797, -0.40409333769472977, 2.1219843545071058, -0.40409333769472977, 1.5688889120969, -0.43711396112220474, -0.45362427283594225, 1.9073503022285185, -0.4701345845496797, 1.890839990514781, -0.4701345845496797, -0.11516288270432372, 1.3707651715320501, -0.09865257099058622, 1.1643862751103315, -0.395838181837861, 1.6101646913812437, 0.2645742867116385, 1.5111028210988189, 0.6195459885569945, -0.46187942869281096, 1.5771440679537687, -0.26375568812796113, 0.5617598975589133, 0.14074694885860736, -0.428858805265336, -0.4701345845496797, -0.428858805265336, 0.702097547125682], 'byte_count': [-0.16364395998370546, -0.16422699175792135, -0.16306793159416483, -0.1584772129395279, -0.16306793159416483, -0.1596660374881543, -0.16287884020793264, -0.16419197483454503, -0.15789768285764963, -0.16422699175792135, -0.15796421501206465, -0.16422699175792135, -0.16242362020404033, -0.16011775579970897, -0.158

({'up': defaultdict(<class 'list'>, {'packet_count': [1.5441234445262937, -0.43711396112220474, 1.3625100156751815, -0.37932787012412356, -0.43711396112220474, 1.469827041814475, 0.536994429988307, 0.39665678042153846, -0.4701345845496797, 0.42967740384901343, 0.6278011444138633, -0.42060364940846723, 0.8011594174081069, -0.2059695971298799, 0.43793255970588213, 0.8259248849787132, 1.63493015895185, -0.42060364940846723, -0.4701345845496797, 0.5204841182745696, -0.04086647999250501, 0.8589455084061881, -0.4701345845496797, -0.395838181837861, 1.0735795606847753, -0.1481835061317987, -0.17294897370240492, 0.30585006599598225, -0.07388710341997999, 1.3542548598183126], 'byte_count': [-0.15919681071491149, -0.16364395998370546, -0.15957761975662907, -0.16347193934761922, -0.16365096336838073, -0.15936314110094907, -0.16070954180476896, -0.16173378681352663, -0.16422699175792135, -0.16081459257489794, -0.16093014842203984, -0.1636089430603291, -0.16083560272892375, -0.16312220782539813, -0

({'up': defaultdict(<class 'list'>, {'packet_count': [-0.4701345845496797, -0.428858805265336, 1.4863373535282125, 0.9497522228317443, 0.3884016245646697, -0.42060364940846723, 0.7598836381237631, 0.15725726057234485, 0.5452495858451758, 0.3388706894234572, -0.45362427283594225, -0.428858805265336, 1.601909535524375, -0.428858805265336, 1.379020327388919, -0.428858805265336, -0.4701345845496797, 0.7186078588394195, 0.30585006599598225, 0.8094145732649757, 0.5122289624177009, -0.428858805265336, -0.4453691169790735, 1.0157934696866942, -0.46187942869281096, -0.21422475298674865, 0.7846491056943694, 1.0735795606847753, 1.0405589372573005, 1.5111028210988189], 'byte_count': [-0.16422699175792135, -0.1631204569792293, -0.159335127562248, -0.16005472533763157, -0.16229580843371674, -0.1636089430603291, -0.1601737828771111, -0.1623045626645608, -0.16142563788781492, -0.1618563460453438, -0.16377002090786025, -0.1636264515220173, -0.15905849386757498, -0.1636264515220173, -0.15589996737902997

({'up': defaultdict(<class 'list'>, {'packet_count': [1.8000332760892248, -0.428858805265336, 1.379020327388919, -0.43711396112220474, -0.4701345845496797, 1.4120409508163938, -0.42060364940846723, 0.8754558201199256, -0.2967763115554361, -0.43711396112220474, 1.5193579769556875, -0.09865257099058622, 2.0559431076521557, -0.3215417791260423, -0.40409333769472977, -0.42060364940846723, 0.9332419111180068, -0.3710727142672548, 1.3707651715320501, -0.43711396112220474, -0.4453691169790735, -0.4453691169790735, -0.4701345845496797, -0.43711396112220474, -0.24724537641422362, 0.5617598975589133, 0.1655124164292136, 0.45444287141961964, -0.46187942869281096, -0.43711396112220474], 'byte_count': [-0.15866980601809771, -0.1636264515220173, -0.15957849517971348, -0.16364395998370546, -0.16422699175792135, -0.15899546340549758, -0.16264422682131122, -0.16018078626178636, -0.1633743296737077, -0.16364395998370546, -0.1592808513310147, -0.16289459782345198, -0.15807977085920655, -0.163383083904551

({'up': defaultdict(<class 'list'>, {'packet_count': [-0.4701345845496797, -0.19771444127301116, 1.5853992238106376, -0.2059695971298799, 1.6184198472381124, -0.43711396112220474, 0.8341800408355818, 0.3718913128509322, 1.0075383138298255, 0.35538100113719473, -0.4701345845496797, 1.692716249949931, -0.4701345845496797, 1.725736873377406, -0.40409333769472977, -0.2967763115554361, 1.7670126526617498, -0.42060364940846723, 1.535868288669425, -0.4453691169790735, -0.4453691169790735, 0.17376757228608233, 0.5287392741314384, 0.8754558201199256, 0.5122289624177009, 0.6443114561276008, 0.6443114561276008, 0.32236037770971976, -0.4701345845496797, 1.2882136129633628], 'byte_count': [-0.16422699175792135, -0.16259870482092198, -0.1592090666380932, -0.1626319708981295, -0.15956098671802532, -0.16364395998370546, -0.16006347956847566, -0.16181782742962983, -0.16044516403327766, -0.1618686019685255, -0.16422699175792135, -0.1583844180925806, -0.16422699175792135, -0.15831438424582797, -0.1604171

In [7]:
local_max_up_bytes = []
local_min_up_bytes = []
local_max_up_packet = []
local_min_up_packet = []
local_max_down_bytes = []
local_min_down_bytes = []
local_max_down_packet = []
local_min_down_packet = []

for scalo in scalos_up:
    local_max_up_bytes.append((get_spikes(scalo[0][0], np.greater), scalo[1]))
    local_min_up_bytes.append((get_spikes(scalo[0][0], np.less), scalo[1]))
    local_max_up_packet.append((get_spikes(scalo[0][1], np.greater), scalo[1]))
    local_min_up_packet.append((get_spikes(scalo[0][1], np.less), scalo[1]))

for scalo in scalos_down:
    local_max_down_bytes.append((get_spikes(scalo[0][0], np.greater), scalo[1]))
    local_min_down_bytes.append((get_spikes(scalo[0][0], np.less), scalo[1]))
    local_max_down_packet.append((get_spikes(scalo[0][1], np.greater), scalo[1]))
    local_min_down_packet.append((get_spikes(scalo[0][1], np.less), scalo[1]))

/home/agro/work/thesis/env/lib/python3.6/site-packages/scipy/signal/_peak_finding.py:68: RuntimeWarning: invalid value encountered in greater
  results &= comparator(main, plus)
/home/agro/work/thesis/env/lib/python3.6/site-packages/scipy/signal/_peak_finding.py:69: RuntimeWarning: invalid value encountered in greater
  results &= comparator(main, minus)
/home/agro/work/thesis/env/lib/python3.6/site-packages/scipy/signal/_peak_finding.py:68: RuntimeWarning: invalid value encountered in less
  results &= comparator(main, plus)
/home/agro/work/thesis/env/lib/python3.6/site-packages/scipy/signal/_peak_finding.py:69: RuntimeWarning: invalid value encountered in less
  results &= comparator(main, minus)


In [57]:
from itertools import groupby
from scipy import stats

def get_stats_numpy(data, zero):
    mean = np.mean(data)
    median = np.median(data)
    std = np.std(data)
    var = np.var(data)
    skew = stats.skew(data)
    kurt = stats.kurtosis(data)
    pc = [25,50,75,90]
    percentiles = np.array(np.percentile(data, pc))
    silences = np.count_nonzero(np.asarray(data)==zero)
    silence_mean = np.mean(list(sum(1 for _ in g) for k, g in groupby(data) if k==zero ))
    longest_silence = max(sum(1 for _ in g) for k, g in groupby(data) if k==zero) if silences > 0 else 0
    shortest_silence = min(sum(1 for _ in g) for k, g in groupby(data) if k==zero) if silences > 0 else 0
    
    #print("Mean: " + str(mean))
    #print("Media: " + str(median))
    #print("StdDev: " + str(std))
    #print("Variance: " + str(var))
    #print("Skewness: " + str(skew))
    #print("Kurtosis: " + str(kurt))
    #print("Pc25: " + str(percentiles[0]))
    #print("Pc50: " + str(percentiles[1]))
    #print("Pc75: " + str(percentiles[2]))
    
    features = np.hstack((mean, median, std, var, skew, kurt, percentiles, silences, silence_mean, longest_silence, shortest_silence))

    return features

# Put it all on a numpy array
def get_features_numpy(info, local_max_up_bytes, local_min_up_bytes, local_max_up_packet, local_min_up_packet, 
                       local_max_down_bytes, local_min_down_bytes, local_max_down_packet, local_min_down_packet, zeros):
    np.set_printoptions(suppress=True)

    result = []

    for idx in range(0, len(info)):
        result.append(
            np.hstack(
                (
                 get_stats_numpy(info[idx][0]['up']['byte_count'], zeros[1]),
                 get_stats_numpy(info[idx][0]['up']['packet_count'], zeros[0]),
                 local_max_up_bytes[idx], local_min_up_bytes[idx],
                 local_max_up_packet[idx], local_min_up_packet[idx],
                 get_stats_numpy(info[idx][0]['down']['byte_count'], zeros[3]),
                 get_stats_numpy(info[idx][0]['down']['packet_count'], zeros[2]),
                 local_max_down_bytes[idx], local_min_down_bytes[idx],
                 local_max_down_packet[idx], local_min_down_packet[idx],
                )
            )
        )
    print(len(result[0]))
    return result

In [58]:
len(local_max_down_bytes[0])

2

In [59]:
samples = get_features_numpy(info, local_max_up_bytes, local_min_up_bytes, local_max_up_packet, local_min_up_packet,
                                    local_max_down_bytes, local_min_down_bytes, local_max_down_packet, local_min_down_packet,
                                    zeros)
samples

/home/agro/work/thesis/env/lib/python3.6/site-packages/numpy/core/fromnumeric.py:2957: RuntimeWarning: Mean of empty slice.
  out=out, **kwargs)
/home/agro/work/thesis/env/lib/python3.6/site-packages/numpy/core/_methods.py:80: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)


TypeError: object of type 'float' has no len()

In [44]:
names = [
            'up_bytes_mean', 'up_bytes_median', 'up_bytes_std', 'up_bytes_var', 'up_bytes_skew', 'up_bytes_kurt',
            'up_bytes_perc25', 'up_bytes_perc50', 'up_bytes_perc75', 'up_bytes_perc90',
            'up_bytes_silences', 'up_bytes_silence_mean', 'up_bytes_longest_silence', 'up_bytes_shortest_silence',
            'up_packet_mean', 'up_packet_median', 'up_packet_std', 'up_packet_var', 'up_packet_skew', 'up_packet_kurt',
            'up_packet_perc25', 'up_packet_perc50', 'up_packet_perc75', 'up_packet_perc90',
            'up_packet_silences', 'up_packet_silence_mean', 'up_packet_longest_silence', 'up_packet_shortest_silence',
            'up_bytes_1max_y', 'up_bytes_2max_y', 'up_bytes_3max_y', 'up_bytes_4max_y', 'up_bytes_5max_y',
            'up_bytes_1max_x', 'up_bytes_2max_x', 'up_bytes_3max_x', 'up_bytes_4max_x', 'up_bytes_5max_x',
            'up_bytes_1min_y', 'up_bytes_2min_y', 'up_bytes_3min_y', 'up_bytes_4min_y', 'up_bytes_5min_y',
            'up_bytes_1min_x', 'up_bytes_2min_x', 'up_bytes_3min_x', 'up_bytes_4min_x', 'up_bytes_5min_x',
            'up_packet_1max_y', 'up_packet_2max_y', 'up_packet_3max_y', 'up_packet_4max_y', 'up_packet_5max_y',
            'up_packet_1max_x', 'up_packet_2max_x', 'up_packet_3max_x', 'up_packet_4max_x', 'up_packet_5max_x',
            'up_packet_1min_y', 'up_packet_2min_y', 'up_packet_3min_y', 'up_packet_4min_y', 'up_packet_5min_y',
            'up_packet_1min_x', 'up_packet_2min_x', 'up_packet_3min_x', 'up_packet_4min_x', 'up_packet_5min_x',

            'down_bytes_mean', 'down_bytes_median', 'down_bytes_std', 'down_bytes_var', 'down_bytes_skew', 'down_bytes_kurt',
            'down_bytes_perc25', 'down_bytes_perc50', 'down_bytes_perc75', 'down_bytes_perc90',
            'down_bytes_silences', 'down_bytes_silence_mean', 'down_bytes_longest_silence', 'down_bytes_shortest_silence',
            'down_packet_mean', 'down_packet_median', 'down_packet_std', 'down_packet_var', 'down_packet_skew', 'down_packet_kurt',
            'down_packet_perc25', 'down_packet_perc50', 'down_packet_perc75', 'down_packet_perc90',
            'down_packet_silences', 'down_packet_silence_mean', 'down_packet_longest_silence', 'down_packet_shortest_silence',
            'down_bytes_1max_y', 'down_bytes_2max_y', 'down_bytes_3max_y', 'down_bytes_4max_y', 'down_bytes_5max_y',
            'down_bytes_1max_x', 'down_bytes_2max_x', 'down_bytes_3max_x', 'down_bytes_4max_x', 'down_bytes_5max_x',
            'down_bytes_1min_y', 'down_bytes_2min_y', 'down_bytes_3min_y', 'down_bytes_4min_y', 'down_bytes_5min_y',
            'down_bytes_1min_x', 'down_bytes_2min_x', 'down_bytes_3min_x', 'down_bytes_4min_x', 'down_bytes_5min_x',
            'down_packet_1max_y', 'down_packet_2max_y', 'down_packet_3max_y', 'down_packet_4max_y', 'down_packet_5max_y',
            'down_packet_1max_x', 'down_packet_2max_x', 'down_packet_3max_x', 'down_packet_4max_x', 'down_packet_5max_x',
            'down_packet_1min_y', 'down_packet_2min_y', 'down_packet_3min_y', 'down_packet_4min_y', 'down_packet_5min_y',
            'down_packet_1min_x', 'down_packet_2min_x', 'down_packet_3min_x', 'down_packet_4min_x', 'down_packet_5min_x'
        ]
    
df = pd.DataFrame(samples, columns=names)

AssertionError: 136 columns passed, passed data had 72 columns